In [2]:
!pip install --upgrade transformers
!pip install pinecone
!pip install openai==0.28
!pip install -U sentence-transformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 1.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.7/9.7 MB 52.3 MB/s eta 0:00:00
  Attempting uninstall: transformers
    Found existing installation: transformers 4.47.1
    Uninstalling transformers-4.47.1:
      Successfully uninstalled transformers-4.47.1
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 427.3/427.3 kB 13.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 87.5/87.5 kB 6.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.5/76.5 kB 4.0 MB/s eta 0:00:00
  Attempting uninstall: openai
    Found existing installation: openai 1.59.6
    Uninstalling openai-1.59.6:
      Successfully uninstalled openai-1.59.6


In [3]:
from transformers import AutoTokenizer, AutoModelForMaskedLM, AutoConfig, pipeline
from sentence_transformers import SentenceTransformer, SimilarityFunction
import torch
import json
import os
import openai

In [4]:
from google.colab import userdata


hf_token = userdata.get('HF_TOKEN')

if hf_token is None:
    raise ValueError("Hugging Face token not found.")

from huggingface_hub import login


login(token=hf_token)

Install embeding model:

In [5]:
model = SentenceTransformer("nomic-ai/modernbert-embed-base", similarity_fn_name=SimilarityFunction.COSINE)

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/210 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/445k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/54.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.26k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/596M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/20.8k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/3.58M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/694 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/296 [00:00<?, ?B/s]

In [6]:
from nltk.tokenize import word_tokenize #text tokenizer
import nltk
nltk.download('punkt')
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


True

Load data from json file:

In [8]:
file_name = "merged_data.json"


with open(file_name, "r") as json_file:
    data = json.load(json_file)

print(data[0])

{'GUID': 1, 'ActName': 'Act Governing Domestic Help And Domestic Employees', 'Section': 'Scope of application', 'Paragraph': '§ 1', 'Text': '. (1) The provisions of this Federal Act shall apply to the employment relationship of employees who provide domestic services for their employer or members of such employer’s household, regardless of whether or not they are residing in the employer’s household. (2) Employees within the meaning of Para 1 above shall include persons who provide services of a more qualified type (domestic employees). (3) In applying this Act, no difference shall be made whether the household is managed by a natural person or legal person for its members or for a third party. However, the Act shall not apply to an employment relationship of employees of legal persons when such relationship is governed by a collective bargaining agreement. (4) The provisions of this Federal Act shall not apply to: a) employment relationships of employees who, in addition to the servic

In [10]:
device = 0 if torch.cuda.is_available() else -1
summarizer = pipeline("summarization", model="facebook/bart-large", device = device)

openai.api_key = userdata.get('OPEN_AI').strip()


Device set to use cuda:0


Chunks with a length of less than 768 tokens (the maximum supported by Pinecone) are not vectorized. Larger chunks are summarized before vectorization using different models based on their size:


*   Chunks up to 1024 tokens are summarized using facebook/bart-large.
*   Chunks exceeding 1024 tokens are summarized using gpt-3.5.
    

This preprocessing ensures that the data is appropriately condensed while preserving its semantic relevance, enabling efficient and accurate vectorization for retrieval.

In [11]:
for par in data:
  print(par['GUID'])
  if len(word_tokenize(par['Text'])) <= 768:
    #normal text
    par["Summary"] = par["Text"]
  else:
    if len(word_tokenize(par['Text'])) >= 1024:
      # gpt
      response = openai.ChatCompletion.create(
      model="gpt-3.5-turbo",
      messages=[
          {"role": "system", "content": "You are a helpful assistant that summarizes text."},
          {"role": "user", "content": f"Summarize the following text:\n{par['Text']}"}
      ],
      max_tokens=768,
      temperature=0.5)
      par["Summary"] = response['choices'][0]['message']['content']
    else:
      # bert
      par["Summary"] = summarizer(par["Text"], max_length=768, do_sample=False,truncation=True)[0]["summary_text"]


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [56]:
data[5]

{'GUID': 6,
 'ActName': 'Act Governing Domestic Help And Domestic Employees',
 'Section': 'General terms',
 'Paragraph': '§ 6',
 'Text': '. (1) Employees are entitled to a leisure period each week which shall commence not later than 2 pm on a working day to be agreed and end upon the time the employee is on duty again on the next following day. On such day, the breaks as defined in Paras (3) and (4) of Section 5 shall be omitted. In addition, employees shall be entitled to an off-duty Sunday once every two weeks. Such leisure period shall commence upon the time the employee goes off duty on Saturday and shall end at the time the employee is on duty again on Monday. (2) On those Sundays which are not off-duty for the employee and on legal holidays, the on-duty period must not exceed 6 hours. On such days, the breaks as defined in Paras (3) and (4) of Section 5 shall be omitted. If the employee is requested to work on a Sunday that would otherwise be off-duty, the next following Sunday s

In [15]:
with open("merged_data_with_summary.json", "w") as json_file:
    json.dump(data, json_file, indent=4, ensure_ascii=False)

In [16]:
embeds = []
for i in range(len(data)):

  embeds.append(model.encode(data[i]["ActName"] + " " + data[i]["Section"] + data[i]["Paragraph"] + " " + data[i]["Summary"]))

print(embeds)


[array([-3.91677767e-02, -6.20798133e-02,  1.69537533e-02,  3.72241959e-02,
       -1.58775225e-02, -3.63076441e-02, -8.76687933e-03,  1.83156561e-02,
       -2.37653106e-02, -4.50303890e-02, -1.06674014e-02, -1.56481843e-02,
        4.57193665e-02, -1.96470767e-02, -1.93601903e-02, -1.29084950e-02,
       -1.42514659e-03, -2.18283050e-02, -6.48598075e-02, -5.63868731e-02,
       -2.24747695e-02, -2.18501166e-02,  3.04292459e-02, -5.94650693e-02,
       -8.17280170e-03,  4.11865814e-03,  3.40618752e-02,  4.65927236e-02,
        4.48015518e-03, -1.33740660e-02, -7.64503554e-02, -7.24162301e-03,
       -2.85012298e-03, -1.17084468e-02,  1.36616090e-02, -1.04858745e-02,
       -8.48562643e-02, -2.92521855e-03,  2.48904694e-02,  2.78865062e-02,
       -6.10319152e-03, -1.66962501e-02,  1.11807827e-02, -2.09907275e-02,
       -4.63632663e-04, -4.95928489e-02, -6.49520159e-02, -2.53674816e-02,
       -2.66920459e-02,  4.85313162e-02,  3.75848673e-02, -6.13635145e-02,
       -2.94331554e-02, 

In [17]:
from pinecone import Pinecone, ServerlessSpec

pc = Pinecone(api_key=userdata.get('PINE'))

Create pinecone Index:

In [22]:
index_name = "rag-data-paragraphs"


pc.create_index(

    name=index_name,

    dimension=768,

    metric="cosine",

    spec=ServerlessSpec(

        cloud="aws",

        region="us-east-1"

    )

)

In [23]:
index = pc.Index(index_name)

Add data to the pincone Index

In [29]:
pinecone_data = []
for i in range(len(embeds)):
  if i % 100 == 0 and i != 0:
    index.upsert(vectors=pinecone_data)
    pinecone_data.clear()
  refs_str = " ".join([str(ref) for ref in data[i]["References"]])
  pinecone_data.append({
      "id" : str(i),
      "values" : embeds[i].tolist(),
      "metadata" : {
          "GUID" : data[i]["GUID"],
          "Section" : data[i]["Section"],
          "Paragraph" : data[i]["Paragraph"],
          "References" : refs_str,
          "Summary" : data[i]["Summary"],
          "ActName" : data[i]["ActName"],
          "Text": "Text:" + data[i]["Text"],
      }
  })
  index.upsert(vectors=pinecone_data)

